In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.make_match1() # 2-1-1
self.make_match2() # 2-1-2
self.make_match3() # 2-1-3
self.make_match4() # 2-1-4
self.make_match5() # 2-1-5

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [3]:
self.turn_type[self.turn_type.node_id=='i8']

node_id    inc_edge_id   out_edge_id turn_type
23      i8  -571500569_01  571500583_02  straight
24      i8  -571500569_01  571500618_01      left
25      i8   571500618_02  571500583_02      left
26      i8   571500618_02  571500617_01  straight
27      i8   571500617_02  571500618_01  straight
28      i8   571500618_02  571500617_01  straight
29      i8   571500617_02  571500618_01  straight
30      i8   571500617_02  571500569_01      left
31      i8   571500583_01  571500617_01      left
32      i8   571500583_01  571500569_01  straight

In [4]:
self.match5 = self.match4.copy()
# 진입진출ID 매칭
for index, row in self.match5.iterrows():
    node_id = self.inter2node[row.inter_no]
    node = self.net.getNode(node_id)
    # 교차로의 모든 (from / to) edges
    inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
    out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
    # 교차로의 모든 (from / to) unit vector
    inc_vecs = []
    for inc_edge in inc_edges:
        start = inc_edge.getShape()[-1]
        end = inc_edge.getShape()[-2]
        inc_vec = np.array(end) - np.array(start)
        inc_vec = inc_vec / (inc_vec ** 2).sum() ** 0.5
        inc_vecs.append(inc_vec)
    out_vecs = []
    for out_edge in out_edges:
        start = out_edge.getShape()[0]
        end = out_edge.getShape()[1]
        out_vec = np.array(end) - np.array(start)
        out_vec = out_vec / (out_vec ** 2).sum() ** 0.5
        out_vecs.append(out_vec)
    # 진입각, 진출각 불러오기
    if not pd.isna(row.inc_angle):
        inc_angle = int(row.inc_angle)
        out_angle = int(row.out_angle)
        # 방위각을 일반각으로 가공, 라디안 변환, 단위벡터로 변환
        inc_angle = (90 - inc_angle) % 360
        inc_angle = inc_angle * np.pi / 180.
        inc_vec_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
        out_angle = (90 - out_angle) % 360
        out_angle = out_angle * np.pi / 180.
        out_vec_true = np.array([np.cos(out_angle), np.sin(out_angle)])
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs]).argmax()
        out_index = np.array([np.dot(out_vec, out_vec_true) for out_vec in out_vecs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id = out_edges[out_index].getID()
        self.match5.at[index, 'inc_edge_id'] = inc_edge_id
        self.match5.at[index, 'out_edge_id'] = out_edge_id
self.match5['node_id'] = self.match5['inter_no'].map(self.inter2node)
self.match5 = self.match5.sort_values(by=['inter_no','phase_no','ring_type']).reset_index(drop=True)

# n2io2turn : dictionary that maps node_id to io2turn
self.n2io2turn = dict()
for node_id in self.parent_ids:
    turn = self.turn_type[self.turn_type.node_id==node_id]
    io = list(zip(turn.inc_edge_id, turn.out_edge_id))
    # io2turn : dictionary that maps (inc_edge_id, out_edge_id) to turn_type
    io2turn = dict(zip(io, turn.turn_type))
    self.n2io2turn[node_id] = io2turn

# turn_type 지정
for i, row in self.match5.iterrows():
    node_id = row.node_id
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    if not (pd.isna(inc_edge_id) and pd.isna(out_edge_id)):
        turn_type = self.n2io2turn[node_id][(inc_edge_id, out_edge_id)]
        self.match5.at[i, 'turn_type'] = turn_type


In [5]:
self = DailyPreprocessor() 
self.load_data() # 1
self.get_matches() # 2
self.initialize_state() # 2-1

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 초기화 신호가 지정되었습니다. (우회전 : g)


In [6]:
m5 = self.match5[(self.match5.node_id=='i0')]
display(m5)

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   
5       175         3         B        1        동        남       090   
6       175         4         A        5        서        북       270   
7       175         4         B        2        서        동       270   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight  
5       180   571545870_02  571542797_02      i0      left  
6       000   571510153_02  571500487_01      i0      left  
7       090   571510153_02  571545870_01      i0  straight

In [7]:
display(self.match5.head())
display(self.match6.head())
display(self.matching.head())

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
0       175      i0        1        동        남   571545870_02  571542797_02   
1       175      i0        2        서        동   571510153_02  571545870_01   
2       175      i0        3        남        서  -571542797_02  571510153_01   
3       175      i0        4        북        남  -571500487_01  571542797_02   
4       175      i0        5        서        북   571510153_02  571500487_01   

  turn_type  
0      left  
1  straight  
2      left  
3  straight  
4      left

In [8]:
import copy
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1 매칭테이블 생성
self.initialize_state() # 2-2 신호 초기화

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 초기화 신호가 지정되었습니다. (우회전 : g)


In [ ]:
self.p2UPLindices = dict() # parent id to unprotected left index
for parent_id in self.parent_ids:
    init_state = self.node2init[parent_id]
    # 우회전 이동류 인덱스
    indices_right = [i for i in range(len(init_state)) if init_state[i]=='g']
    # from-to가 지정된 이동류 인덱스
    indices_assigned = []
    m5 = self.match5[(self.match5.node_id==parent_id)].dropna(subset=['inc_edge_id', 'out_edge_id'])
    for row in m5.itertuples():
        inc_edge = self.net.getEdge(row.inc_edge_id)
        out_edge = self.net.getEdge(row.out_edge_id)
        conns = inc_edge.getConnections(out_edge)
        indices = [conn for conn in conns if conn.getTLLinkIndex()>=0]
        indices = [conn for conn in conns if conn.getJunctionIndex()>=0]
        indices = [conn.getTLLinkIndex() for conn in conns]
        indices_assigned.extend(indices)
    # 좌회전 이동류 인덱스
    indices_left = []
    for row in self.turn_type[self.turn_type.turn_type=='left'].itertuples():
        inc_edge = self.net.getEdge(row.inc_edge_id)
        out_edge = self.net.getEdge(row.out_edge_id)
        conns = inc_edge.getConnections(out_edge)
        indices = [conn for conn in conns if conn.getTLLinkIndex()>=0]
        indices = [conn for conn in conns if conn.getJunctionIndex()>=0]
        indices = [conn.getTLLinkIndex() for conn in conns]
        indices_left.extend(indices)
    # 비보호좌회전 인덱스 (unprotected left index)
    UPLindices = list((set(range(len(init_state))) - set(indices_right) - set(indices_assigned)).intersection(indices_left))
    self.p2UPLindices[parent_id] = UPLindices


In [24]:
self.p2UPLindices = dict() # parent id to unprotected left index
for parent_id in self.parent_ids:
    init_state = self.node2init[parent_id]
    # 우회전 이동류 인덱스
    indices_right = [i for i in range(len(init_state)) if init_state[i]=='g']
    # from-to가 지정된 이동류 인덱스
    indices_assigned = []
    m5 = self.match5[(self.match5.node_id==parent_id)].dropna(subset=['inc_edge_id', 'out_edge_id'])
    for row in m5.itertuples():
        inc_edge = self.net.getEdge(row.inc_edge_id)
        out_edge = self.net.getEdge(row.out_edge_id)
        conns = inc_edge.getConnections(out_edge)
        indices = [conn for conn in conns if conn.getTLLinkIndex()>=0]
        indices = [conn for conn in conns if conn.getJunctionIndex()>=0]
        indices = [conn.getTLLinkIndex() for conn in conns]
        indices_assigned.extend(indices)
    # 좌회전 이동류 인덱스
    indices_left = []
    for row in self.turn_type[self.turn_type.turn_type=='left'].itertuples():
        inc_edge = self.net.getEdge(row.inc_edge_id)
        out_edge = self.net.getEdge(row.out_edge_id)
        conns = inc_edge.getConnections(out_edge)
        indices = [conn for conn in conns if conn.getTLLinkIndex()>=0]
        indices = [conn for conn in conns if conn.getJunctionIndex()>=0]
        indices = [conn.getTLLinkIndex() for conn in conns]
        indices_left.extend(indices)
    # 비보호좌회전 인덱스 (unprotected left index)
    UPLindices = list((set(range(len(init_state))) - set(indices_right) - set(indices_assigned)).intersection(indices_left))
    self.p2UPLindices[parent_id] = dict()
    for UPLindex in UPLindices:
        node = self.net.getNode(parent_id)
        conns = node.getConnections()
        conns = [conn for conn in conns if conn.getTLLinkIndex() == UPLindex]
        inc_edge_ids = [conn.getFrom().getID() for conn in conns]
        self.p2UPLindices[parent_id][UPLindex] = inc_edge_ids

In [23]:
for UPLindex in UPLindices:
    node = self.net.getNode(parent_id)
    conns = node.getConnections()
    conns = [conn for conn in conns if conn.getTLLinkIndex() == UPLindex]
    inc_edge_ids = [conn.getFrom().getID() for conn in conns]


parent_id = self.parent_ids[5]
UPLindices = self.p2UPLindices[parent_id]
UPLindex = UPLindices[0]
print(UPLindex)

node = self.net.getNode(parent_id)
conns = node.getConnections()
conns = [conn for conn in conns if conn.getTLLinkIndex() == UPLindex]
conn = conns[0]
inc_edge = conn.getFrom().getID()
print(inc_edge)

2
571542073_01
